In [1]:
from direct.showbase.ShowBase import ShowBase
from panda3d.core import AmbientLight, DirectionalLight, LightAttrib
from panda3d.core import NodePath
from panda3d.core import LVector3
from panda3d.core import TextureStage
from panda3d.core import Vec4, LineSegs, GeomNode, GeomVertexFormat, GeomVertexData, GeomVertexWriter, Geom, GeomLinestrips, GeomTrifans, GeomTristrips
from direct.interval.IntervalGlobal import *
from direct.gui.DirectGui import *
import numpy as np

In [2]:
from math import pi
import time
import json

In [3]:
EARTH_RADIUS = 6371 # (km)
GM_earth = 3.986004418 * 10**14 # standard gravitational parameter for earth, m^3/s^2

In [4]:
FPS = 60 # 60 frames per second
SECS_PER_YEAR = 15 # 15 seconds / year
EARTH_MODEL_R = 0.852763 # taken from model
ORBIT_POINT_CNT = 90 # decrease if too slow
SCALING_FACTOR = EARTH_MODEL_R / EARTH_RADIUS

In [5]:
# OrbitInfo
# takes TLE as input
# see this image for details:
# https://miro.medium.com/max/1194/1*dYa0T_eg6DZa03Hv9OHaCw.png
# helpful reference for calculations: https://blog.hardinglabs.com/tle-to-kep.html

# newton rhapson method for root finding
def newton_rhapson(f, df, x, delta=0.00001, max_iter=1000, n=0):
    if abs(f(x)) < delta:
        return x
    if n > max_iter:
        raise RuntimeError("Unable to find root")
    return newton_rhapson(f, df, x - f(x)/df(x), delta, max_iter, n + 1)
    
class OrbitInfo:
    def __init__(self, name, line1, line2):
        self.name = name
        self.TLE = "\n".join([name, line1, line2])
        
        # line1 parsing
        self.id_year = int(line1[9:11])
        self.epoch_year = int(line1[18:20])
        self.epoch = float(line1[20:32])
        
        # line2 parsing
        self.inclination = (float(line2[8:16]) * (pi / 180)) % pi
        self.right_ascension = float(line2[17:25]) * (pi / 180)
        self.eccentricity = float(line2[26:33]) * 0.0000001
        self.argument_perigee = float(line2[34:42]) * (pi / 180)
        self.mean_anomaly = float(line2[43:51]) * (pi / 180)
        self.mean_motion = float(line2[52:63])
        
        # extra calculations
        self.year = 2000 + self.epoch_year if self.epoch_year < 57 else 1900 + self.epoch_year
        self.launch_year = 2000 + self.id_year if self.id_year < 57 else 1900 + self.id_year
        
        self.period = (24 * 60 * 60) * (1/self.mean_motion)
        self.semi_major_axis = ((self.period/(2*pi))**2 * (GM_earth/1000**3))**(1/3)
        
        # obtain eccentric anomaly using kepler's equation
        self.eccentric_anomaly = newton_rhapson(
            lambda E: E - self.eccentricity * np.sin(E) - self.mean_anomaly, # f
            lambda E: 1.0 - self.eccentricity * np.cos(E), # df
            self.mean_anomaly # initial value
        )
        
        # obtain true anomaly from eccentric anomaly
        self.true_anomaly = np.arccos(
            (np.cos(self.eccentric_anomaly) - self.eccentricity) /
            (1 - self.eccentricity * np.cos(self.eccentric_anomaly))
        )
    
    def to_line_segs(self):
        rads = np.linspace(0, 2 *  pi, ORBIT_POINT_CNT)
        r = (self.semi_major_axis * (1 - self.eccentricity ** 2)) / (1 + self.eccentricity * np.cos(rads))
    
        u = self.argument_perigee + rads
        sin_u = np.sin(u)
        cos_u = np.cos(u)
        sin_ra = np.sin(self.right_ascension)
        cos_ra = np.cos(self.right_ascension)
        sin_i = np.sin(self.inclination)
        cos_i = np.cos(self.inclination)
        U = np.array([
            cos_u * cos_ra - sin_u * sin_ra * cos_i,
            cos_u * sin_ra + sin_u * cos_ra * cos_i,
            sin_u * sin_i
        ])
        
        points = U * r
        points *= SCALING_FACTOR

        points = points.T
        
        return np.split(points, ORBIT_POINT_CNT // 2)
    
    def to_curr_pos(self):
        Rx = np.matrix([
            [1, 0, 0],
            [0, np.cos(self.inclination), -np.sin(self.inclination)],
            [0, np.sin(self.inclination), np.cos(self.inclination)]
        ])

        ang = self.right_ascension + self.argument_perigee
        Rz = np.matrix([
            [np.cos(ang), -np.sin(ang), 0],
            [np.sin(ang), np.cos(ang), 0],
            [0, 0, 1]
        ])
        
        r = (self.semi_major_axis * (1 - self.eccentricity ** 2)) / (1 + self.eccentricity * np.cos(self.true_anomaly))
        pos = (Rx * Rz * np.matrix([
            r * np.cos(self.true_anomaly),
            r * np.sin(self.true_anomaly),
            0
        ]).T).flatten()

        pos *= SCALING_FACTOR
        return pos.tolist()[0]

    @staticmethod
    def from_debris(debris):
        try:
            return OrbitInfo(debris["ON"], debris["TLE1"], debris["TLE2"])
        except:
            return None
    
    @staticmethod
    def from_satellite(satellite):
        try:
            if "payload" not in satellite:
                return OrbitInfo(satellite["name"], satellite["TLE1"], satellite["TLE2"])
            return OrbitInfo(satellite["payload"], satellite["TLE1"], satellite["TLE2"])
        except:
            return None

In [6]:
with open("data/TLEdebris.json") as f:
    debris_data = json.load(f)
with open("data/TLE2.json") as f:
    satellites_data = json.load(f)

In [7]:
debris = [OrbitInfo.from_debris(d) for d in debris_data]
satellites = [OrbitInfo.from_satellite(s) for s in satellites_data]
debris = [d for d in debris if d]
satellites = [s for s in satellites if s]

from collections import defaultdict
debris_map = defaultdict(lambda: [])
sat_map = defaultdict(lambda: [])

for d in debris:
    debris_map[d.launch_year].append(d)
for s in satellites:
    sat_map[s.launch_year].append(s)

start = min([min([d.launch_year for d in debris]), min([s.launch_year for s in satellites])])

In [8]:
earth_rot = 365 / (1 * SECS_PER_YEAR * FPS) # should finish a full rotation 

class OrbitRing():
    def __init__(self, ring, box, year):
        self.ring = ring
        self.box = box
        self.year = year

class SpaceDebris(ShowBase):
    geo_id = 0

    def __init__(self, start_year):
        ShowBase.__init__(self)
        self.year = start_year
        self.visible = []
        self.spin = True

        self.title = OnscreenText(
            text=f"{self.year}",
            parent=base.a2dBottomCenter,
            fg=(1, 1, 1, 1), shadow=(0, 0, 0, .5),
            pos=(0, .1), scale=.1
        )
        
        base.disableMouse()
        camera.setPosHpr(0, -25, 0, 0, 0, 0)

        base.setBackgroundColor(0,0,0)
        
        self.load_models()
        self.load_controls()

        for s in sat_map[self.year]:
            orbit_ring = self.plot_line_segs(s.to_line_segs(), (0,0,1))
            if self.spin:
                orbit_box = None
            else:
                orbit_box = self.plot_box(s.to_curr_pos(), (0.01, 0.01, 0.01), (0,0,1))
            self.visible.append(OrbitRing(orbit_ring, orbit_box, s.launch_year))
        for d in debris_map[self.year]:
            orbit_ring = self.plot_line_segs(d.to_line_segs(), (1,0,0))
            if self.spin:
                orbit_box = None
            else:
                orbit_box = self.plot_box(d.to_curr_pos(), (0.01, 0.01, 0.01), (1,0,0))
            self.visible.append(OrbitRing(orbit_ring, orbit_box, d.launch_year))
        
        taskMgr.doMethodLater(1 / FPS, self.tick, 'SpaceDebris_tick', appendTask=True)
        
    def load_models(self):
        self.earth = loader.loadModel("models/earth.dae")
        self.earth.reparentTo(render)
        self.earth.setHpr(0,90,0)

        diffuse = TextureStage('diffuse')
        self.earth.setTexture(diffuse, loader.loadTexture('textures/Earth_Diffuse_6K.jpg'))
        normal = TextureStage('normal')
        normal.setMode(TextureStage.MNormal)
        self.earth.setTexture(normal, loader.loadTexture('textures/Earth_NormalNRM_6K.jpg'))
        clouds = TextureStage('clouds')
        clouds.setMode(TextureStage.MAdd)
        self.earth.setTexture(clouds, loader.loadTexture('textures/Earth_Clouds_6K.jpg'))
        haze = TextureStage('haze')
        haze.setMode(TextureStage.MGlow)
        self.earth.setTexture(haze, loader.loadTexture('textures/Blue_Haze.jpg'))
        
        self.earth_bounds = self.earth.getBounds()
        
    def load_controls(self):
        self.accept('arrow_right', self.next_year)
        self.accept('arrow_left', self.prev_year)
        self.accept('arrow_up', self.zoom_in)
        self.accept('arrow_down', self.zoom_out)
        self.accept('s', self.enable_spin)
    
    def prev_year(self):
        self.year -= 1
        for ring in self.visible:
            if ring.year > self.year:
                ring.ring.removeNode()
                if ring.box != None:
                    ring.box.removeNode()
        self.visible = [r for r in self.visible if r.year <= self.year]
        self.title.text = f"{self.year}"
        
    def next_year(self):
        self.year += 1
        for s in sat_map[self.year]:
            orbit_ring = self.plot_line_segs(s.to_line_segs(), (0,0,1))
            if self.spin:
                orbit_box = None
            else:
                orbit_box = self.plot_box(s.to_curr_pos(), (0.01, 0.01, 0.01), (0,0,1))
            self.visible.append(OrbitRing(orbit_ring, orbit_box, s.launch_year))
        for d in debris_map[self.year]:
            orbit_ring = self.plot_line_segs(d.to_line_segs(), (1,0,0))
            if self.spin:
                orbit_box = None
            else:
                orbit_box = self.plot_box(d.to_curr_pos(), (0.01, 0.01, 0.01), (1,0,0))
            self.visible.append(OrbitRing(orbit_ring, orbit_box, d.launch_year))
        self.title.text = f"{self.year}"
    
    def zoom_in(self):
        x,y,z = camera.getPos()
        camera.setPos(x, y + 5, z)
    
    def zoom_out(self):
        x,y,z = camera.getPos()
        camera.setPos(x, y - 5, z)
        
    def enable_spin(self):
        self.spin = True
        for r in self.visible:
            if r.box != None:
                r.box.removeNode()
    
    # pain
    def plot_line_segs(self, lines, color=(1,0,0)):
        v3 = GeomVertexFormat.getV3()
        vert_data = GeomVertexData("lol", v3, Geom.UHStatic)
        vert_data.set_num_rows(2 * len(lines))
        vertex = GeomVertexWriter(vert_data, "vertex")
        prim = GeomLinestrips(Geom.UHStatic)
        
        for line in lines:
            vertex.add_data3f(line[0,0],line[0,1],line[0,2])
            vertex.add_data3f(line[1,0],line[1,1],line[1,2])

        prim.add_consecutive_vertices(0, len(lines)*2)
        prim.close_primitive()
        
        geom = Geom(vert_data)
        geom.add_primitive(prim)
        
        node = GeomNode(f"line seg {SpaceDebris.geo_id}")
        SpaceDebris.geo_id += 1
        node.addGeom(geom)
        
        node_path = render.attachNewNode(node)
        node_path.set_render_mode_thickness(1)
        node_path.set_color(*color)
        node_path.reparentTo(render)

        return node_path
    
    def plot_box(self, origin, size = (1,1,1), color = (1,0,0)):
        node = GeomNode(f"box {SpaceDebris.geo_id}")
        sX = size[0] / 2.0
        sY = size[1] / 2.0
        sZ = size[2] / 2.0

        gFormat = GeomVertexFormat.getV3()
        boxVertexData = GeomVertexData("vertices", gFormat, Geom.UHDynamic)

        boxVertexWriter = GeomVertexWriter(boxVertexData, "vertex")

        # Front
        boxVertexWriter.addData3f(sX, sY, sZ)
        boxVertexWriter.addData3f(sX, sY, -sZ)
        boxVertexWriter.addData3f(-sX, sY, -sZ)
        boxVertexWriter.addData3f(-sX, sY, sZ)

        #Back
        boxVertexWriter.addData3f(-sX, -sY, sZ)
        boxVertexWriter.addData3f(-sX, -sY, -sZ)
        boxVertexWriter.addData3f(sX, -sY, -sZ)
        boxVertexWriter.addData3f(sX, -sY, sZ)

        #Top
        boxVertexWriter.addData3f(-sX, sY, sZ)
        boxVertexWriter.addData3f(-sX, -sY, sZ)
        boxVertexWriter.addData3f(sX, -sY, sZ)
        boxVertexWriter.addData3f(sX, sY, sZ)

        #Bottom
        boxVertexWriter.addData3f(sX, sY, -sZ)
        boxVertexWriter.addData3f(sX, -sY, -sZ)
        boxVertexWriter.addData3f(-sX, -sY, -sZ)
        boxVertexWriter.addData3f(-sX, sY, -sZ)

        #Right
        boxVertexWriter.addData3f(sX, sY, sZ)
        boxVertexWriter.addData3f(sX, -sY, sZ)
        boxVertexWriter.addData3f(sX, -sY, -sZ)
        boxVertexWriter.addData3f(sX, sY, -sZ)

        #Left
        boxVertexWriter.addData3f(-sX, sY, -sZ)
        boxVertexWriter.addData3f(-sX, -sY, -sZ)
        boxVertexWriter.addData3f(-sX, -sY, sZ)
        boxVertexWriter.addData3f(-sX, sY, sZ)

        boxTris = GeomTristrips(Geom.UHStatic)
        boxTris.addVertex(0)#(1)
        boxTris.addVertex(1)#(2)
        boxTris.addVertex(3)#(0)
        boxTris.addVertex(2)#(3)
        boxTris.closePrimitive()

        boxTris.addVertex(5)
        boxTris.addVertex(6)
        boxTris.addVertex(4)
        boxTris.addVertex(7)
        boxTris.closePrimitive()

        boxTris.addVertex(9)
        boxTris.addVertex(10)
        boxTris.addVertex(8)
        boxTris.addVertex(11)
        boxTris.closePrimitive()

        boxTris.addVertex(13)
        boxTris.addVertex(14)
        boxTris.addVertex(12)
        boxTris.addVertex(15)
        boxTris.closePrimitive()

        boxTris.addVertex(16) #(17)
        boxTris.addVertex(17) #(18)
        boxTris.addVertex(19) #(16)
        boxTris.addVertex(18) #(19)
        boxTris.closePrimitive()

        boxTris.addVertex(21)
        boxTris.addVertex(22)
        boxTris.addVertex(20)
        boxTris.addVertex(23)
        boxTris.closePrimitive()

        geom = Geom(boxVertexData)
        geom.addPrimitive(boxTris)

        node.addGeom(geom)
        
        node_path = render.attachNewNode(node)
        node_path.set_render_mode_thickness(1)
        node_path.setPos(*origin)
        node_path.set_color(*color)
        node_path.reparentTo(render)

        return node_path
        
    def tick(self, task):
        if self.spin:
            h,p,r = self.earth.getHpr()
            self.earth.setHpr(h, p, (r - earth_rot) % 360)

            for ring in self.visible:
                h,p,r = ring.ring.getHpr()
                ring.ring.setHpr((h + earth_rot) % 360, p, r)
        
        return task.again

In [9]:
demo = SpaceDebris(start)
demo.run()

Known pipe types:
  glxGraphicsPipe
(1 aux display modules not yet loaded.)
AL lib: (EE) GetLoadedHrtf: Invalid header in /usr/share/openal/hrtf/Default HRTF.mhr: "MinPHR03"
AL lib: (EE) GetLoadedHrtf: Failed to load /usr/share/openal/hrtf/Default HRTF.mhr


SystemExit: 

/home/bryce/.local/lib/python3.10/site-packages/IPython/core/interactiveshell.py:3441: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
